In [0]:
%pip install prophet
%pip install folium

%restart_python

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
from pyspark.sql.functions import col
import pandas as pd
from prophet import Prophet
import folium
from datetime import datetime, timedelta

In [0]:
%sql
SELECT * FROM weatherHistory

datetime temperature_2m precipitation rain wind_speed_10m soil_temperature_0_to_7cm soil_moisture_0_to_7cm PlantID Unit latitude longitude 2025-02-01T00:00:00.000Z 23.7695 0.0 0.0 9.726664 24.0195 0.357 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T01:00:00.000Z 26.219501 0.0 0.0 8.305396 25.369501 0.355 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T02:00:00.000Z 27.7695 0.0 0.0 11.995349 26.3195 0.354 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T03:00:00.000Z 28.6695 0.1 0.1 15.702356 27.2695 0.353 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T04:00:00.000Z 29.5195 0.0 0.0 18.762356 28.119501 0.351 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T05:00:00.000Z 30.219501 0.0 0.0 19.42416 28.7695 0.348 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T06:00:00.000Z 30.7695 0.0 0.0 19.440832 29.4195 0.345 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T07:00:00.000Z 30.7695 0.1 0.1 19.320465 29.719501 0.343 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T08:00:00.000Z 30.6695 0.1 0.1 17.548845 29.7695 0.341 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T09:00:00.000Z 30.0695 0.0 0.0 16.733225 29.5695 0.339 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T10:00:00.000Z 27.869501 0.4 0.4 16.521805 28.9195 0.341 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T11:00:00.000Z 27.2695 0.0 0.0 13.321216 28.119501 0.341 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T12:00:00.000Z 26.6695 0.0 0.0 12.599999 27.469501 0.341 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T13:00:00.000Z 26.4195 0.0 0.0 13.878688 27.2695 0.331 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T14:00:00.000Z 26.3195 0.0 0.0 13.31635 26.9195 0.331 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T15:00:00.000Z 26.1695 0.0 0.0 11.542478 26.619501 0.331 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T16:00:00.000Z 25.969501 0.0 0.0 11.542478 26.4195 0.331 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T17:00:00.000Z 25.719501 0.0 0.0 10.429132 26.219501 0.331 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T18:00:00.000Z 25.5195 0.0 0.0 10.32924 26.0695 0.331 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T19:00:00.000Z 25.3195 0.0 0.0 9.796366 25.9195 0.332 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T20:00:00.000Z 25.0695 0.0 0.0 9.387651 25.7695 0.332 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T21:00:00.000Z 24.8195 0.0 0.0 8.9873905 25.619501 0.332 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T22:00:00.000Z 24.5195 0.0 0.0 9.703319 25.469501 0.332 IDN04013 Unit_13 -2.833569 104.829788 2025-02-01T23:00:00.000Z 24.469501 0.0 0.0 9.437563 25.3195 0.332 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T00:00:00.000Z 24.8195 0.0 0.0 11.238113 25.3195 0.332 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T01:00:00.000Z 26.5195 0.0 0.0 8.536252 26.4195 0.332 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T02:00:00.000Z 27.8195 0.0 0.0 14.230248 27.119501 0.331 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T03:00:00.000Z 28.719501 0.1 0.1 18.934254 27.8195 0.33 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T04:00:00.000Z 29.1695 0.1 0.1 19.513195 28.2695 0.329 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T05:00:00.000Z 29.9195 0.1 0.1 19.272614 28.9195 0.327 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T06:00:00.000Z 29.969501 0.1 0.1 19.272614 29.3195 0.326 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T07:00:00.000Z 30.219501 0.1 0.1 18.526888 29.6695 0.324 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T08:00:00.000Z 29.469501 0.1 0.1 17.95404 29.5695 0.323 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T09:00:00.000Z 28.7695 0.0 0.0 13.979871 29.1695 0.322 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T10:00:00.000Z 27.8195 0.0 0.0 10.272623 28.619501 0.322 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T11:00:00.000Z 27.1695 0.0 0.0 8.777653 28.0695 0.322 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T12:00:00.000Z 26.4195 0.0 0.0 10.018743 27.469501 0.322 IDN04013 Unit_13 -2.833569 104.829788 2025-02-02T13:00:00

In [0]:
from pyspark.sql.functions import col
import pandas as pd
from prophet import Prophet

In [0]:


unit_forecasts = {}

for unit_row in _sqldf.select("Unit").distinct().collect():

    unit_value = unit_row["Unit"]  # extract the actual string
    df_unit = _sqldf.filter(_sqldf["Unit"] == unit_value).select("datetime", "temperature_2m") \
        .withColumnRenamed("datetime", "ds") \
        .withColumnRenamed("temperature_2m", "y")
    df_temp_pd = df_unit.toPandas()
    model = Prophet()
    model.fit(df_temp_pd)
    
    future = model.make_future_dataframe(periods=168, freq="H")  # next 7 days
    forecast = model.predict(future)
    forecast["Unit"] = unit_value
    
    unit_forecasts[unit_value] = forecast


02:54:47 - cmdstanpy - INFO - Chain [1] start processing
02:54:48 - cmdstanpy - INFO - Chain [1] done processing
02:54:50 - cmdstanpy - INFO - Chain [1] start processing
02:54:53 - cmdstanpy - INFO - Chain [1] done processing
02:54:55 - cmdstanpy - INFO - Chain [1] start processing
02:54:56 - cmdstanpy - INFO - Chain [1] done processing
02:54:58 - cmdstanpy - INFO - Chain [1] start processing
02:55:00 - cmdstanpy - INFO - Chain [1] done processing
02:55:02 - cmdstanpy - INFO - Chain [1] start processing
02:55:04 - cmdstanpy - INFO - Chain [1] done processing
02:55:07 - cmdstanpy - INFO - Chain [1] start processing
02:55:08 - cmdstanpy - INFO - Chain [1] done processing
02:55:10 - cmdstanpy - INFO - Chain [1] start processing
02:55:11 - cmdstanpy - INFO - Chain [1] done processing
02:55:13 - cmdstanpy - INFO - Chain [1] start processing
02:55:15 - cmdstanpy - INFO - Chain [1] done processing
02:55:17 - cmdstanpy - INFO - Chain [1] start processing
02:55:18 - cmdstanpy - INFO - Chain [1]

In [0]:
summary_list = []

for unit,df in unit_forecasts.items():
    df_next168 = df.tail(168)  # keep last 168 rows = future only
    avg_temp = df_next168["yhat"].mean()
    min_temp = df_next168["yhat_lower"].min()
    max_temp = df_next168["yhat_upper"].max()

    unit_row = _sqldf.filter(_sqldf["Unit"] == unit).select("latitude", "longitude").first()
    
    lat = unit_row["latitude"]
    lon = unit_row["longitude"]

    summary_list.append({
        "Unit": unit,
        "lat": lat,
        "lon": lon,
        "avg_temp": avg_temp,
        "min_temp": min_temp,
        "max_temp": max_temp
    })

map_df_pd = pd.DataFrame(summary_list)
map_df = spark.createDataFrame(map_df_pd)
    

In [0]:
m = folium.Map(location=[pd.to_numeric(map_df.toPandas()["lat"], errors='coerce').mean(), pd.to_numeric(map_df.toPandas()["lon"], errors='coerce').mean()], zoom_start=6)

for _, row in map_df.toPandas().iterrows():
    unit_id = row["Unit"]
    forecast_unique = unit_forecasts[unit_id]

    now = datetime.now()  # or use timezone-aware datetime if needed
    end_time = now + timedelta(hours=23)

    forecast_24h = forecast_unique[(forecast_unique['ds'] >= now) & (forecast_unique['ds'] < end_time)]
    # Create forecast table for this unit
    popup_html = """
    <b>🌤️ Hourly Forecast (24H)</b><br>
    <table style='
        font-size: 12px;
        border-collapse: collapse;
        width: 100%;
        border: 1px solid #ddd;
        border-radius: 6px;
        overflow: hidden;
    '>
    <thead style='background-color: #f2f2f2;'>
    <tr>
        <th style='padding: 8px; text-align: left; border-bottom: 1px solid #ddd;'>Time</th>
        <th style='padding: 8px; text-align: right; border-bottom: 1px solid #ddd;'>Temp (°C)</th>
        <th style='padding: 8px; text-align: right; border-bottom: 1px solid #ddd;'>↓</th>
        <th style='padding: 8px; text-align: right; border-bottom: 1px solid #ddd;'>↑</th>
    </tr>
    </thead>
    <tbody>
    """

    for i, (_, f_row) in enumerate(forecast_24h.iterrows()):
        bg = "#ffffff" if i % 2 == 0 else "#f9f9f9"
        popup_html += f"<tr style='background-color: {bg};'>"
        popup_html += f"<td style='padding: 6px; border-bottom: 1px solid #ddd;'>{f_row['ds'].strftime('%Y-%m-%d %H:%M')}</td>"
        popup_html += f"<td style='padding: 6px; text-align: right; border-bottom: 1px solid #ddd;'>{f_row['yhat']:.1f}</td>"
        popup_html += f"<td style='padding: 6px; text-align: right; border-bottom: 1px solid #ddd;'>{f_row['yhat_lower']:.1f}</td>"
        popup_html += f"<td style='padding: 6px; text-align: right; border-bottom: 1px solid #ddd;'>{f_row['yhat_upper']:.1f}</td>"
        popup_html += "</tr>"

    popup_html += "</tbody></table>"

    # Add marker with dynamic forecast popup
    folium.Marker(
        location=[row["lat"], row["lon"]],
        popup=folium.Popup(popup_html, max_width=400),
        tooltip=row["Unit"],
        icon=folium.Icon(color="blue", icon="cloud")
    ).add_to(m)

m


In [0]:
# Assuming your dictionary is called `unit_forecasts`
combined_df = pd.concat(unit_forecasts.values(), ignore_index=True)
spark_df = spark.createDataFrame(combined_df)


In [0]:
from pyspark.sql.functions import col, lit, concat
df_selected = _sqldf.select("Unit", "PlantID", "latitude", "longitude")


joined_df = spark_df.join(df_selected, on = "Unit", how="left")

joined_df = joined_df.withColumn("pkey", concat(col("Unit").cast("string"), lit("_"), col("ds").cast("string")))



In [0]:
# Create Table
joined_df.write.format("delta").mode("overwrite").option("overwriteSchema", "true").saveAsTable("default.weatherForecastAllUnits")